In [1]:
%pip install moviepy
%pip install --upgrade scenedetect[opencv]
%pip install opencv-python

  Using cached moviepy-1.0.3-py3-none-any.whl
  Using cached decorator-4.4.2-py2.py3-none-any.whl (9.2 kB)
  Using cached proglog-0.1.10-py3-none-any.whl (6.1 kB)
     -------------------------------------- 312.7/312.7 kB 9.8 MB/s eta 0:00:00
  Using cached imageio_ffmpeg-0.4.8-py3-none-win_amd64.whl (22.6 MB)
  Attempting uninstall: decorator
    Found existing installation: decorator 5.1.1
    Uninstalling decorator-5.1.1:
      Successfully uninstalled decorator-5.1.1
Note: you may need to restart the kernel to use updated packages.
  Using cached scenedetect-0.6.1-py3-none-any.whl (115 kB)
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [2]:
data_dir = "G:/ModelscopeTraining/Datasets/subset_v20230528_1848" # the input directory path

Crop Black Bars in folder /toCrop

In [ ]:
# Detect and Crop black bars in /toCrop

import os
import subprocess


# Input
toCrop_dir = f"{data_dir}/toCrop"

# Output
cropped_dir = f"{data_dir}/cropped"

input_dir = toCrop_dir
output_dir = cropped_dir

# Make sure output directory exists
os.makedirs(output_dir, exist_ok=True)

# Iterate over all video files in the input directory
for filename in os.listdir(input_dir):
    # Skip files that are not videos
    if not (filename.endswith(".mp4") or filename.endswith(".webm") or filename.endswith(".mkv") or filename.endswith(".avi") or filename.endswith(".mov")):
        continue

    input_file = os.path.join(input_dir, filename)
    output_file = os.path.join(output_dir, os.path.splitext(filename)[0] + ".mp4")

    # Step 1: Use FFmpeg to detect black bars
    command = ["ffmpeg", "-i", input_file, "-vf", "cropdetect=24:16:0", "-f", "null", "-"]
    try:
        cropdetect_result = subprocess.run(command, capture_output=True, text=True, errors='ignore')
    except Exception as e:
        print(f"Error executing command {command}. Error: {e}")
        continue

    # Parse the cropdetect result to get the crop parameters
    try:
        if cropdetect_result.stderr is not None:
            crop_params = [line for line in cropdetect_result.stderr.split('\n') if 'crop=' in line][-1].split('crop=')[1].split(' ')[0]
        else:
            crop_params = None
    except IndexError:
        crop_params = None

    # Step 2: If black bars are detected, crop them out
    if crop_params:
        command = ["ffmpeg", "-i", input_file, "-vf", f"crop={crop_params}", output_file]
    else:
        # If no black bars are detected, just convert the video to .mp4
        command = ["ffmpeg", "-i", input_file, "-c:v", "libx264", "-crf", "23", "-preset", "veryfast", output_file]
    
    try:
        subprocess.run(command)
    except Exception as e:
        print(f"Error executing command {command}. Error: {e}")



Cut N Crop (process files in /toCutNcrop)

In [ ]:
#Split clips in /toCutnCrop

import os
import subprocess

# Input
toSplit_dir = f"{data_dir}/toCutNcrop

# Output
split_dir = f"{data_dir}/splittedb4crop"

input_dir = toSplit_dir
output_dir = split_dir

# Get a list of video files in the input directory
video_files = [
    file for file in os.listdir(input_dir)
    if file.endswith((".mkv", ".mp4", ".avi", ".webm", ".mov"))
]

# Iterate over each video file
for video_file in video_files:
    # Construct the full paths for input and output files
    input_path = os.path.join(input_dir, video_file)
    output_path = os.path.join(output_dir, os.path.splitext(video_file)[0])

    # Create the output directory if it doesn't exist
    os.makedirs(output_path, exist_ok=True)

    # Run SceneDetect CLI via subprocess
    subprocess.run(
        [
            "scenedetect",
            "-i",
            input_path,
            "-o",
            output_path,
            "detect-content",
            "-t",
            "27",  # Set detection threshold (adjust as needed)
            "list-scenes",
            "split-video",
        ],
        capture_output=True,
        text=True
    )

    print(f"Scenes detected and clips split for {video_file}")


In [ ]:
# Crop black bars in /toCutnCrop

import os
import subprocess


# Input
toCrop_dir = f"{data_dir}/splittedb4crop"

# Output
cropped_dir = f"{data_dir}/splitNcropped"

input_dir = toCrop_dir
output_dir = cropped_dir

# Make sure output directory exists
os.makedirs(output_dir, exist_ok=True)

# Iterate over all video files in the input directory
for filename in os.listdir(input_dir):
    # Skip files that are not videos
    if not (filename.endswith(".mp4") or filename.endswith(".webm") or filename.endswith(".mkv") or filename.endswith(".avi") or filename.endswith(".mov")):
        continue

    input_file = os.path.join(input_dir, filename)
    output_file = os.path.join(output_dir, os.path.splitext(filename)[0] + ".mp4")

    # Step 1: Use FFmpeg to detect black bars
    command = ["ffmpeg", "-i", input_file, "-vf", "cropdetect=24:16:0", "-f", "null", "-"]
    try:
        cropdetect_result = subprocess.run(command, capture_output=True, text=True, errors='ignore')
    except Exception as e:
        print(f"Error executing command {command}. Error: {e}")
        continue

    # Parse the cropdetect result to get the crop parameters
    try:
        if cropdetect_result.stderr is not None:
            crop_params = [line for line in cropdetect_result.stderr.split('\n') if 'crop=' in line][-1].split('crop=')[1].split(' ')[0]
        else:
            crop_params = None
    except IndexError:
        crop_params = None

    # Step 2: If black bars are detected, crop them out
    if crop_params:
        command = ["ffmpeg", "-i", input_file, "-vf", f"crop={crop_params}", output_file]
    else:
        # If no black bars are detected, just convert the video to .mp4
        command = ["ffmpeg", "-i", input_file, "-c:v", "libx264", "-crf", "23", "-preset", "veryfast", output_file]
    
    try:
        subprocess.run(command)
    except Exception as e:
        print(f"Error executing command {command}. Error: {e}")



Split Clean Clips

In [ ]:
#Split clips in /clean

import os
import subprocess

# Input
toSplit_dir = f"{data_dir}/clean"

# Output
split_dir = f"{data_dir}/splitted"

input_dir = toSplit_dir
output_dir = split_dir

# Get a list of video files in the input directory
video_files = [
    file for file in os.listdir(input_dir)
    if file.endswith((".mkv", ".mp4", ".avi", ".webm", ".mov"))
]

# Iterate over each video file
for video_file in video_files:
    # Construct the full paths for input and output files
    input_path = os.path.join(input_dir, video_file)
    output_path = os.path.join(output_dir, os.path.splitext(video_file)[0])

    # Create the output directory if it doesn't exist
    os.makedirs(output_path, exist_ok=True)

    # Run SceneDetect CLI via subprocess
    subprocess.run(
        [
            "scenedetect",
            "-i",
            input_path,
            "-o",
            output_path,
            "detect-content",
            "-t",
            "27",  # Set detection threshold (adjust as needed)
            "list-scenes",
            "split-video",
        ],
        capture_output=True,
        text=True
    )

    print(f"Scenes detected and clips split for {video_file}")


In [ ]:
#Split clips in /cropped

import os
import subprocess

# Input
toSplit_dir = f"{data_dir}/cropped"

# Output
split_dir = f"{data_dir}/splitted"

input_dir = toSplit_dir
output_dir = split_dir

# Get a list of video files in the input directory
video_files = [
    file for file in os.listdir(input_dir)
    if file.endswith((".mkv", ".mp4", ".avi", ".webm", ".mov"))
]

# Iterate over each video file
for video_file in video_files:
    # Construct the full paths for input and output files
    input_path = os.path.join(input_dir, video_file)
    output_path = os.path.join(output_dir, os.path.splitext(video_file)[0])

    # Create the output directory if it doesn't exist
    os.makedirs(output_path, exist_ok=True)

    # Run SceneDetect CLI via subprocess
    subprocess.run(
        [
            "scenedetect",
            "-i",
            input_path,
            "-o",
            output_path,
            "detect-content",
            "-t",
            "27",  # Set detection threshold (adjust as needed)
            "list-scenes",
            "split-video",
        ],
        capture_output=True,
        text=True
    )

    print(f"Scenes detected and clips split for {video_file}")


Filter and Crop to Size (didnt use, instead manually selected clips in file explorer based on length)

In [ ]:
# Filter and crop Splitted 

import os
import subprocess
import re
from concurrent.futures import ThreadPoolExecutor
from moviepy.editor import VideoFileClip

# Input
clean_dir = f"{data_dir}/splitted"

# Output
finished_dir = f"{data_dir}/finished"

input_dir = clean_dir
output_dir = finished_dir

# Make sure output directory exists
os.makedirs(output_dir, exist_ok=True)

# Step 1: Setup environment
min_res_width = 640  # minimum resolution width
min_res_height = 360  # minimum resolution height
min_duration = 1  # minimum duration in seconds
max_duration = 2  # maximum duration in seconds
out_res_width = 320  # output resolution width
out_res_height = 320  # output resolution height
num_threads = 8  # number of threads to use for processing

# Step 2: Iterate through all files
file_list = []

# Instead of using os.listdir(), use os.walk() to also search in subdirectories
for root, dirs, files in os.walk(input_dir):
    for file_name in files:
        if file_name.endswith((".mp4", ".mov", ".webm", ".mkv", ".avi")):
            file_path = os.path.join(root, file_name)

            cmd_width = f'ffprobe -v error -select_streams v:0 -show_entries stream=width -of default=noprint_wrappers=1:nokey=1 "{file_path}"'
            cmd_height = f'ffprobe -v error -select_streams v:0 -show_entries stream=height -of default=noprint_wrappers=1:nokey=1 "{file_path}"'
            
            try:
                width_output = subprocess.check_output(cmd_width, shell=True).decode("utf-8").strip()
                height_output = subprocess.check_output(cmd_height, shell=True).decode("utf-8").strip()

                # If width or height could not be determined, skip this file
                if width_output == '' or height_output == '':
                    print(f"Width or height could not be determined for file {file_name}. Skipping...")
                    continue

                width = int(float(width_output))
                height = int(float(height_output))

                            # Try getting the duration with ffprobe first
                try:
                    cmd_duration = f'ffprobe -v error -select_streams v:0 -show_entries stream=duration -of default=noprint_wrappers=1:nokey=1 "{file_path}"'
                    duration = int(float(subprocess.check_output(cmd_duration, shell=True).decode("utf-8").strip()))
                except:
                    # If ffprobe fails, use moviepy
                    clip = VideoFileClip(file_path)
                    duration = int(clip.duration)
                    clip.close()  # Ensure to close the clip to free up system resources
                
                if width >= min_res_width and height >= min_res_height and duration >= min_duration:
                    file_list.append(file_path)

            except subprocess.CalledProcessError as e:
                print(f"Error processing file {file_path}: {e}")

            try:
                if width >= min_res_width and height >= min_res_height and min_duration <= duration <= max_duration:
                    file_list.append(file_path)
            except ValueError as e:
                print(f"Error: Could not retrieve width, height, or duration for file {file_path}. Skipping...")


# Step 3: Write to .txt file
with open(os.path.join(output_dir, "video_list.txt"), "w") as f:
    for file_name in file_list:
        f.write("%s\n" % file_name)




In [ ]:
# Step 4 & 5: Scale, crop videos and save (multithreaded)
def process_video(file_path):  # Renamed argument for clarity
    file_name = os.path.basename(file_path)  # Get file name for clean_name
    clean_name = re.sub(r"\W+", "", file_name)
    input_path = file_path  # Corrected
    output_path = os.path.join(output_dir, clean_name)
    output_path = os.path.splitext(output_path)[0] + ".mp4"
    cmd = f'ffmpeg -i "{input_path}" -vf "scale={out_res_width}:{out_res_height}:force_original_aspect_ratio=increase,crop={out_res_width}:{out_res_height},setsar=1" -b:v 1M "{output_path}"'
    try:
        subprocess.run(cmd, shell=True, check=True)
        print(f"Processing complete for file: {file_path}")  # Changed to file_path for clarity
    except subprocess.CalledProcessError as e:
        print(f"Error processing file {file_path}: {e}")  # Changed to file_path for clarity

# Use ThreadPoolExecutor to process videos in parallel
with ThreadPoolExecutor(max_workers=num_threads) as executor:
    executor.map(process_video, file_list)

In [ ]:
# Filter and crop Splitted Selects (manually selected from file explorer and copied to folder)

import os
import subprocess
import re
from concurrent.futures import ThreadPoolExecutor
from moviepy.editor import VideoFileClip

# Input
clean_dir = f"{data_dir}/splittedSelects"

# Output
finished_dir = f"{data_dir}/finished"

input_dir = clean_dir
output_dir = finished_dir

# Make sure output directory exists
os.makedirs(output_dir, exist_ok=True)

# Step 1: Setup environment
min_res_width = 640  # minimum resolution width
min_res_height = 360  # minimum resolution height
min_duration = 1  # minimum duration in seconds
out_res_width = 320  # output resolution width
out_res_height = 320  # output resolution height
num_threads = 8  # number of threads to use for processing

# Step 2: Iterate through all files
file_list = []

for file_name in os.listdir(input_dir):
    if file_name.endswith((".mp4", ".mov", ".webm", ".mkv", ".avi")):
        file_path = os.path.join(input_dir, file_name)

        cmd_width = f'ffprobe -v error -select_streams v:0 -show_entries stream=width -of default=noprint_wrappers=1:nokey=1 "{file_path}"'
        cmd_height = f'ffprobe -v error -select_streams v:0 -show_entries stream=height -of default=noprint_wrappers=1:nokey=1 "{file_path}"'
        
        try:
            width = int(float(subprocess.check_output(cmd_width, shell=True).decode("utf-8").strip()))
            height = int(float(subprocess.check_output(cmd_height, shell=True).decode("utf-8").strip()))
            
            # Try getting the duration with ffprobe first
            try:
                cmd_duration = f'ffprobe -v error -select_streams v:0 -show_entries stream=duration -of default=noprint_wrappers=1:nokey=1 "{file_path}"'
                duration = int(float(subprocess.check_output(cmd_duration, shell=True).decode("utf-8").strip()))
            except:
                # If ffprobe fails, use moviepy
                clip = VideoFileClip(file_path)
                duration = int(clip.duration)
                clip.close()  # Ensure to close the clip to free up system resources
            
            if width >= min_res_width and height >= min_res_height and duration >= min_duration:
                file_list.append(file_name)
        except ValueError as e:
            print(f"Error: Could not retrieve width, height, or duration for file {file_name}. Skipping...")
        except subprocess.CalledProcessError as e:
            print(f"Error processing file {file_name}: {e}")


# Step 3: Write to .txt file
with open(os.path.join(output_dir, "video_list.txt"), "w") as f:
    for file_name in file_list:
        f.write("%s\n" % file_name)

# Step 4 & 5: Scale, crop videos and save (multithreaded)
def process_video(file_name):
    clean_name = re.sub(r"\W+", "", file_name)
    input_path = os.path.join(input_dir, file_name)
    output_path = os.path.join(output_dir, clean_name)
    output_path = os.path.splitext(output_path)[0] + ".mp4"
    cmd = f'ffmpeg -i "{input_path}" -vf "scale={out_res_width}:{out_res_height}:force_original_aspect_ratio=increase,crop={out_res_width}:{out_res_height},setsar=1" -b:v 1M "{output_path}"'
    try:
        subprocess.run(cmd, shell=True, check=True)
        print(f"Processing complete for file: {file_name}")
    except subprocess.CalledProcessError as e:
        print(f"Error processing file {file_name}: {e}")

# Use ThreadPoolExecutor to process videos in parallel
with ThreadPoolExecutor(max_workers=num_threads) as executor:
    executor.map(process_video, file_list)


Just Scale and crop a folder of manually selected videos, select 15 random scenes from each clip

In [2]:
# Scale and Crop Selects (manually selected from file explorer and copied to folder)

import os
import re
import random
import subprocess
from concurrent.futures import ThreadPoolExecutor
from collections import defaultdict

# Input
input_dir = f"{data_dir}/splittedSelects"

# Output
output_dir = f"{data_dir}/finished"

# Ensure output directory exists
os.makedirs(output_dir, exist_ok=True)

# Video parameters
out_res_width = 320  # output resolution width
out_res_height = 320  # output resolution height
num_threads = 8  # number of threads to use for processing

# Number of scenes to process per video
num_scenes = 15

# Valid video file extensions
valid_extensions = ['.mp4']

def process_video(file_name):
    clean_name = re.sub(r"\W+", "", file_name)
    input_path = os.path.join(input_dir, file_name)
    output_path = os.path.join(output_dir, clean_name)
    output_path = os.path.splitext(output_path)[0] + ".mp4"
    cmd = f'ffmpeg -i "{input_path}" -vf "scale={out_res_width}:{out_res_height}:force_original_aspect_ratio=increase,crop={out_res_width}:{out_res_height},setsar=1" -b:v 1M "{output_path}"'
    try:
        subprocess.run(cmd, shell=True, check=True)
        print(f"Processing complete for file: {file_name}")
    except subprocess.CalledProcessError as e:
        print(f"Error processing file {file_name}: {e}")

def process_all_videos_in_dir():
    file_list = os.listdir(input_dir)
    video_dict = defaultdict(list)
    
    # Group videos by base name
    for file_name in file_list:
        if any(file_name.endswith(ext) for ext in valid_extensions):
            base_name = re.match(r"(.*?)-Scene-\d+", file_name)
            if base_name:
                video_dict[base_name.group(1)].append(file_name)

    # Process num_scenes random scenes from each video
    with ThreadPoolExecutor(max_workers=num_threads) as executor:
        for video_list in video_dict.values():
            if len(video_list) > num_scenes:
                video_list = random.sample(video_list, num_scenes)
            for file_name in video_list:
                executor.submit(process_video, file_name)

# Process all videos in the input directory
process_all_videos_in_dir()


Processing complete for file: 'Left, Right, Left, Right'-79727688-Scene-005.mp4Processing complete for file: 'Left, Right, Left, Right'-79727688-Scene-017.mp4

Processing complete for file: 'Left, Right, Left, Right'-79727688-Scene-014.mp4
Processing complete for file: 'Left, Right, Left, Right'-79727688-Scene-006.mp4
Processing complete for file: 'Left, Right, Left, Right'-79727688-Scene-003.mp4
Processing complete for file: 'Left, Right, Left, Right'-79727688-Scene-002.mp4
Processing complete for file: 'Left, Right, Left, Right'-79727688-Scene-018.mp4
Processing complete for file: 'Left, Right, Left, Right'-79727688-Scene-009.mp4
Processing complete for file: 'Left, Right, Left, Right'-79727688-Scene-019.mp4
Processing complete for file: 'Machine'  -30-100912126-Scene-010.mp4
Processing complete for file: 'Machine'  -30-100912126-Scene-011.mp4
Processing complete for file: 'Machine'  -30-100912126-Scene-018.mp4
Processing complete for file: 'Machine'  -30-100912126-Scene-015.mp4
Proc

Run Video-BLIP2-Preprocessor

In [1]:
import subprocess

preprocessLocation= 'C:/Users/cerspense/Documents/AI/Video-BLIP2-Preprocessor/preprocess.py'
videoDirectory = 'G:/ModelscopeTraining/Datasets/subset_v20230528_1848/Selects_15Scenes_320x320'
configName = 'subset_v20230528_15S_320x320'
promptsPerClip = '2'

# Define the command to run your Python script with flags
command = ['python', preprocessLocation, '--video_directory', videoDirectory, '--config_name', configName, '--config_save_name', configName, '--prompt_amount', promptsPerClip ]

# Start the subprocess and capture its output
process = subprocess.Popen(command, stdout=subprocess.PIPE, stderr=subprocess.STDOUT)

# Read and print the output line by line as the script runs
while True:
    output = process.stdout.readline().decode().strip()
    if output == '' and process.poll() is not None:
        break
    if output:
        print(output)

# Wait for the subprocess to finish
process.wait()

# Get the return code of the subprocess
return_code = process.returncode

print("Script finished with return code:", return_code)


Loading BLIP2
Loading checkpoint shards: 100%|██████████| 2/2 [00:07<00:00,  3.79s/it]
Processing videos in G:/ModelscopeTraining/Datasets/subset_v20230528_1848/Selects_15Scenes_320x320: 0it [00:00, ?it/s]
Processing 112AnywhereOfficialMusicVideofLghl1Ma1IScene001mp4.mp4:   0%|          | 0/2 [00:00<?, ?it/s]
Processing 112AnywhereOfficialMusicVideofLghl1Ma1IScene001mp4.mp4:  50%|█████     | 1/2 [00:02<00:02,  2.45s/it]
Processing 112AnywhereOfficialMusicVideofLghl1Ma1IScene001mp4.mp4: 100%|██████████| 2/2 [00:03<00:00,  1.52s/it]
Processing 112AnywhereOfficialMusicVideofLghl1Ma1IScene004mp4.mp4:   0%|          | 0/2 [00:00<?, ?it/s]
Processing 112AnywhereOfficialMusicVideofLghl1Ma1IScene004mp4.mp4:  50%|█████     | 1/2 [00:00<00:00,  1.76it/s]
Processing 112AnywhereOfficialMusicVideofLghl1Ma1IScene004mp4.mp4: 100%|██████████| 2/2 [00:01<00:00,  1.79it/s]
Processing 112AnywhereOfficialMusicVideofLghl1Ma1IScene006mp4.mp4:   0%|          | 0/2 [00:00<?, ?it/s]
Processing 112AnywhereOffic

Train

In [2]:
import subprocess

trainpyLocation= 'C:/Users/cerspense/Documents/AI/Text-To-Video-Finetuning/train.py'
configLocation = 'C:/Users/cerspense/Documents/AI/csp-t2vDataprep/finetuneConfigs/subset_v20230528_15S_320x320.yaml'

# Define the command to run your Python script with flags
command = ['python', trainpyLocation, '--config', configLocation]

# Start the subprocess and capture its output
process = subprocess.Popen(command, stdout=subprocess.PIPE, stderr=subprocess.STDOUT)

# Read and print the output line by line as the script runs
while True:
    output = process.stdout.readline().decode().strip()
    if output == '' and process.poll() is not None:
        break
    if output:
        print(output)

# Wait for the subprocess to finish
process.wait()

# Get the return code of the subprocess
return_code = process.returncode

print("Script finished with return code:", return_code)

c:\Users\cerspense\.conda\envs\text2video-finetune\lib\site-packages\accelerate\accelerator.py:249: FutureWarning: `logging_dir` is deprecated and will be removed in version 0.18.0 of 🤗 Accelerate. Use `project_dir` instead.
warnings.warn(
c:\Users\cerspense\.conda\envs\text2video-finetune\lib\site-packages\accelerate\accelerator.py:359: UserWarning: `log_with=tensorboard` was passed but no supported trackers are currently installed.
warnings.warn(f"`log_with={log_with}` was passed but no supported trackers are currently installed.")
05/29/2023 21:55:13 - INFO - __main__ - Distributed environment: NO
Num processes: 1
Process index: 0
Local process index: 0
Device: cuda
Mixed precision type: fp16
Traceback (most recent call last):
File "c:\Users\cerspense\.conda\envs\text2video-finetune\lib\site-packages\diffusers\configuration_utils.py", line 356, in load_config
config_file = hf_hub_download(
File "c:\Users\cerspense\.conda\envs\text2video-finetune\lib\site-packages\huggingface_hub\uti